In [8]:
import json
import os
import sys

import pydantic
from pydantic.v1 import BaseModel, Extra, Field

import fhir.resources
from fhir.resources import construct_fhir_element
from fhir.resources import FHIRAbstractModel
from fhir.resources.observation import Observation
from fhir.resources.observation import ObservationComponent
from fhir.resources.quantity import Quantity
from fhir.resources.patient import Patient
from fhir.resources.reference import Reference
from fhir.resources.coding import Coding
from fhir.resources.codeableconcept import CodeableConcept

FHIRAbstractModel.Config.extra = Extra.allow

In [59]:
code = {
    "coding": [
      {
        "system": "http://loinc.org",
        "code": "85354-9",
        "display": "Blood pressure panel with all children optional"
      }
    ],
    "text": "Blood pressure systolic & diastolic"
  }

category =  {
      "coding": [
        {
          "system": "http://terminology.hl7.org/CodeSystem/observation-category",
          "code": "vital-signs",
          "display": "Vital Signs"
        }
      ]
    }

systolic = ObservationComponent(**{
      "code": {
        "coding": [
          {
            "system": "http://loinc.org",
            "code": "8480-6",
            "display": "Systolic blood pressure"
          },
          {
            "system": "http://snomed.info/sct",
            "code": "271649006",
            "display": "Systolic blood pressure"
          },
          {
            "system": "http://acme.org/devices/clinical-codes",
            "code": "bp-s",
            "display": "Systolic Blood pressure"
          }
        ]
      },
      "valueQuantity": {
        "value": 107,
        "unit": "mmHg",
        "system": "http://unitsofmeasure.org",
        "code": "mm[Hg]"
      },
      "interpretation": [
        {
          "coding": [
            {
              "system": "http://terminology.hl7.org/CodeSystem/v3-ObservationInterpretation",
              "code": "N",
              "display": "normal"
            }
          ],
          "text": "Normal"
        }
      ]
    }
)

diastolic = ObservationComponent(**{
      "code": {
        "coding": [
          {
            "system": "http://loinc.org",
            "code": "8462-4",
            "display": "Diastolic blood pressure"
          }
        ]
      },
      "valueQuantity": {
        "value": 60,
        "unit": "mmHg",
        "system": "http://unitsofmeasure.org",
        "code": "mm[Hg]"
      },
      "interpretation": [
        {
          "coding": [
            {
              "system": "http://terminology.hl7.org/CodeSystem/v3-ObservationInterpretation",
              "code": "L",
              "display": "low"
            }
          ],
          "text": "Below low normal"
        }
      ]
    }
)

In [ ]:
blood_data = {
    "active": True,
    "status": "final",
    "effectiveDateTime" : "2012-09-17",
    "code": code,
    "category": [CodeableConcept(**category)],
    "component": [systolic, diastolic]
}

blood_pressure = Observation(**blood_data)

In [55]:
blood_pressure.subject = Reference()

In [56]:
blood_pressure.subject.reference = "Patient/example"

In [57]:
blood_pressure.subject

Reference(resource_type='Reference', fhir_comments=None, extension=None, id=None, display=None, display__ext=None, identifier=None, reference='Patient/example', reference__ext=None, type=None, type__ext=None)

blood_pressure.json()

## Heart Rate

In [11]:
from datetime import datetime

with open("measurements.csv") as f:
    measurements = f.readlines()

# TODO: fix date format
date = datetime.now()

bundle = []

for i, quantity in enumerate(measurements):
    bundle.append(Observation(**{
  "resourceType" : "Observation",
  "id" : "heart-rate",
  "meta" : {
    "profile" : ["http://hl7.org/fhir/StructureDefinition/vitalsigns"]
  },
  "text" : {
    "status" : "generated",
    "div" : "<div xmlns=\"http://www.w3.org/1999/xhtml\"><p><b>Generated Narrative: Observation</b><a name=\"heart-rate\"> </a><a name=\"hcheart-rate\"> </a></p><div style=\"display: inline-block; background-color: #d9e0e7; padding: 6px; margin: 4px; border: 1px solid #8da1b4; border-radius: 5px; line-height: 60%\"><p style=\"margin-bottom: 0px\">Resource Observation &quot;heart-rate&quot; </p><p style=\"margin-bottom: 0px\">Profile: <a href=\"vitalsigns.html\">Vital Signs Profile</a></p></div><p><b>status</b>: final</p><p><b>category</b>: Vital Signs <span style=\"background: LightGoldenRodYellow; margin: 4px; border: 1px solid khaki\"> (<a href=\"http://terminology.hl7.org/5.5.0/CodeSystem-observation-category.html\">Observation Category Codes</a>#vital-signs)</span></p><p><b>code</b>: Heart rate <span style=\"background: LightGoldenRodYellow; margin: 4px; border: 1px solid khaki\"> (<a href=\"https://loinc.org/\">LOINC</a>#8867-4)</span></p><p><b>subject</b>: <a href=\"patient-example.html\">Patient/example</a> &quot;Peter CHALMERS&quot;</p><p><b>effective</b>: 1999-07-02</p><p><b>value</b>: 44 beats/minute<span style=\"background: LightGoldenRodYellow\"> (Details: UCUM code /min = '/min')</span></p></div>"
  },
  "status" : "final",
  "category" : [{
    "coding" : [{
      "system" : "http://terminology.hl7.org/CodeSystem/observation-category",
      "code" : "vital-signs",
      "display" : "Vital Signs"
    }],
    "text" : "Vital Signs"
  }],
  "code" : {
    "coding" : [{
      "system" : "http://loinc.org",
      "code" : "8867-4",
      "display" : "Heart rate"
    }],
    "text" : "Heart rate"
  },
  "subject" : {
    "reference" : "Patient/example"
  },
  "effectiveDateTime" : date,
  "valueQuantity" : {
    "value" : quantity,
    "unit" : "beats/minute",
    "system" : "http://unitsofmeasure.org",
    "code" : "/min"
  }
}))

bundle

[Observation(resource_type='Observation', fhir_comments=None, id='heart-rate', implicitRules=None, implicitRules__ext=None, language=None, language__ext=None, meta=Meta(resource_type='Meta', fhir_comments=None, extension=None, id=None, lastUpdated=None, lastUpdated__ext=None, profile=['http://hl7.org/fhir/StructureDefinition/vitalsigns'], profile__ext=None, security=None, source=None, source__ext=None, tag=None, versionId=None, versionId__ext=None), contained=None, extension=None, modifierExtension=None, text=Narrative(resource_type='Narrative', fhir_comments=None, extension=None, id=None, div='<div xmlns="http://www.w3.org/1999/xhtml"><p><b>Generated Narrative: Observation</b><a name="heart-rate"> </a><a name="hcheart-rate"> </a></p><div style="display: inline-block; background-color: #d9e0e7; padding: 6px; margin: 4px; border: 1px solid #8da1b4; border-radius: 5px; line-height: 60%"><p style="margin-bottom: 0px">Resource Observation &quot;heart-rate&quot; </p><p style="margin-bottom: